In [1]:
#%run input/Format.ipynb
import ROOT as root
from array import array
root.gErrorIgnoreLevel = root.kFatal
import pandas as pd
%jsroot on

Welcome to JupyROOT 6.30/06


In [2]:
iOption0 = 1 # piminus, electron

In [3]:
colors=[1,2,4,root.kGreen+2,root.kMagenta,root.kOrange+4,root.kGray,root.kCyan]
central_bins = [0,95,0,20,20,40,40,60,60,100]
N_centr = int(len(central_bins)/2)
pt_boarders = [0.2,0.3,0.4,0.5,0.6,0.7,0.9,1.1,1.4,1.9,2.5,3.5,5.0]
N_pt = len(pt_boarders)-1
file_path="/home/yoren/bnl/PHENIX/ee/AuAu/"
file_names=["my-100M_piminus_single_hagedorn_04-5_v0.root","my-100M_pi0_gg_embed_helios_new_04-6_v0.root","my-10M_bbbar_pythia_v7.root","my-50M_ccbar_pythia_v0.root"]
code_path="../AnaTrain/Run14AuAuLeptonComby/"
file_name=file_names[iOption0]
outfilenames= ['pionminus','electron',',positron','positron']#output
filename=outfilenames[iOption0]
part_ids=[9,3,3,3]
part_id = part_ids[iOption0]
part_name = ["e^{+}","e^{-}"]

In [4]:
root.gSystem.Load(code_path+"MyEvent_C.so")

0

In [5]:
root.gROOT.ProcessLine(
f"TFile *input = new TFile(\"{file_path+file_name}\", \"READ\");\
TTree *T = (TTree *)input->Get(\"tree\");\
MyDileptonAnalysis::MyEvent *myevent = 0;\
TBranch *br = T->GetBranch(\"MyEvent\");\
br->SetAddress(&myevent);\
MyDileptonAnalysis::MyEventContainer *event_container = new MyDileptonAnalysis::MyEventContainer();\
event_container->InitEvent();\
event_container->GetHistsFromFile(\"{code_path}field_map.root\");\
"
); 
from ROOT import myevent, br, event_container

File opened at ../AnaTrain/Run14AuAuLeptonComby/field_map.root


mcid: 2 - positron, 3 - electron, 8 - pion+, 9 - pion minus

In [6]:
geant3dict = {
  2: "positron",
  3: "electron",
  5: "+muon",
  6: "-muon",
  8: "+pion",
  9: "-pion",
  11: "+kaon",
  12: "-kaon",
  14: "proton",
  15: "antiproton"
}

In [7]:
N_real_ev = br.GetEntries()
print(N_real_ev)
good_event_counter = 0
soso_event_counter = 0 
for ievent in range(N_real_ev):
    if good_event_counter>10000: break
    myevent.ClearEvent()
    br.GetEntry(ievent)
    event_container.SetEvent(myevent)
    if not myevent.GetNtrack(): continue
            
    n_hits = myevent.GetNVTXhit()
    jhit=0
    for ihit in range(n_hits):
        if myevent.GetVTXHitEntry(jhit).GetSensor() == 1 :
            myevent.RemoveVTXHitEntry(jhit)
        else: jhit+=1
    
    event_container.correct_beam_offset()
    event_container.Associate_Hits_to_Leptons(5,5,5)
    for itrack in range(myevent.GetNtrack()):
        if myevent.GetEntry(itrack).GetPtPrime()>0.4 and myevent.GetEntry(itrack).GetTrkQuality()>62 and myevent.GetEntry(itrack).GetMcId()>1 and myevent.GetEntry(itrack).GetMcId()<10:
            soso_event_counter+=1
    do_continue = False
    if event_container.GetNBDThit()>0:
        do_continue = True
    if not do_continue:
        continue
    good_event_counter+=event_container.GetNBDThit()
    if True : print(f"Nevent: {ievent}, centrality: {myevent.GetCentrality()}, N VTX hit: {myevent.GetNVTXhit()}, Ntracks: {myevent.GetNtrack()}, NBDTtracks: {event_container.GetNBDThit()}") 

    for ipart in range(event_container.GetNBDThit()):
        print("N hits:",  event_container.GetBDTHitEntry(ipart).GetNBDThit(), ", pt:", round(event_container.GetBDTHitEntry(ipart).GetPt(),3),\
              ", id:",  geant3dict[myevent.GetEntry(ipart).GetMcId()])
        for ibdthit in range(event_container.GetBDTHitEntry(ipart).GetNBDThit()):
            bdthit = event_container.GetBDTHitEntry(ipart).GetBDTHitEntry(ibdthit)
            print(ibdthit, round(bdthit.Getsdphi(0),3),",",round(bdthit.Getsdphi(1),3),",",round(bdthit.Getsdphi(2),3),",",round(bdthit.Getsdphi(3),3),";",\
                  round(bdthit.GetIsTrue(0),3),",",round(bdthit.GetIsTrue(1),3),",",round(bdthit.GetIsTrue(2),3),",",round(bdthit.GetIsTrue(3),3))
    for ipart in range(myevent.GetNgentrack()):
        print(myevent.GetGenTrack(ipart).GetPt())

8156638
Nevent: 35, centrality: 67.0, N VTX hit: 5, Ntracks: 2, NBDTtracks: 2
N hits: 1 , pt: 0.314 , id: electron
0 -1.487 , -1.208 , 2.213 , -10.0 ; 1.0 , 1.0 , 1.0 , 0.0
N hits: 1 , pt: 1.836 , id: positron
0 0.207 , 0.132 , -0.473 , -10.0 ; 1.0 , 1.0 , 1.0 , 0.0
2.135359048843384
1.196331262588501
Nevent: 48, centrality: 48.0, N VTX hit: 18, Ntracks: 2, NBDTtracks: 1
N hits: 10 , pt: 0.188 , id: positron
0 -4.744 , -1.011 , -0.584 , -10.0 ; 1.0 , 1.0 , 1.0 , 0.0
1 -2.641 , -3.013 , -0.584 , -10.0 ; 1.0 , 1.0 , 1.0 , 0.0
2 -4.744 , -1.011 , -0.914 , -0.433 ; 1.0 , 1.0 , 1.0 , 1.0
3 -2.641 , -3.013 , -0.914 , -0.433 ; 1.0 , 1.0 , 1.0 , 1.0
4 -4.744 , -1.011 , 1.807 , -1.09 ; 1.0 , 1.0 , 1.0 , 0.0
5 -2.641 , -3.013 , 1.807 , -1.09 ; 1.0 , 1.0 , 1.0 , 0.0
6 -4.744 , -1.319 , -10.0 , -0.433 ; 1.0 , 1.0 , 1.0 , 0.0
7 -2.641 , -2.639 , -10.0 , -0.433 ; 1.0 , 1.0 , 1.0 , 0.0
8 -4.744 , 0.491 , -10.0 , -1.09 ; 1.0 , 1.0 , 0.0 , 0.0
9 -2.641 , -0.829 , -10.0 , -1.09 ; 1.0 , 1.0 , 0.0 , 0.0
2

In [8]:
print(good_event_counter,soso_event_counter, ievent)

10001 179076 332109


In [9]:
data_array = []
N_real_ev = br.GetEntries()
print(N_real_ev)
good_event_counter = 0
for ievent in range(N_real_ev):
    if good_event_counter>6000: break
    myevent.ClearEvent()
    br.GetEntry(ievent)
    event_container.SetEvent(myevent)
    if not myevent.GetNtrack(): continue
    counter = 1
    while counter< myevent.GetNVTXhit()-1:
        for ihit in range(myevent.GetNVTXhit()):
            if myevent.GetVTXHitEntry(ihit).GetSensor() == 1 :
                #print("kek")
                myevent.RemoveVTXHitEntry(ihit)
                break
            else :
                counter=ihit
            
    n_hits = myevent.GetNVTXhit()
    for ihit in range(n_hits):
        if myevent.GetVTXHitEntry(ihit).GetSensor() == 1 :
            myevent.RemoveVTXHitEntry(ihit)

    n_hits = myevent.GetNVTXhit()
    for ihit in range(n_hits):
        if myevent.GetVTXHitEntry(ihit).GetSensor() == 1 :
            print("keks")
            myevent.RemoveVTXHitEntry(ihit)
   
    event_container.correct_beam_offset()
    event_container.Associate_Hits_to_Leptons(5,5,5)
    soso_event_counter+=1
    do_continue = False
    for ipart in range(myevent.GetNtrack()):
        if event_container.GetNBDThit()>0:
            do_continue = True
    if not do_continue:
        continue
    good_event_counter+=1
    for ipart in range(event_container.GetNBDThit()):
        BDTpart  = event_container.GetBDTHitEntry(ipart)
        for ibdthit in range(BDTpart.GetNBDThit()):
            
            bdthit = event_container.GetBDTHitEntry(ipart).GetBDTHitEntry(ibdthit)
            data_array.append([BDTpart.GetNBDThit(), BDTpart.GetPt(), BDTpart.GetPhi0(), BDTpart.GetThe0(), BDTpart.GetPhiDC(), BDTpart.GetZDC(), \
                               BDTpart.GetAlpha(), BDTpart.GetEcore(), BDTpart.GetCentrality(), BDTpart.GetCharge(), BDTpart.GetArm(),\
                               bdthit.Getsdphi(0), bdthit.Getsdthe(0), bdthit.GetIsTrue(0), bdthit.GetSecondHitPhiR(0), bdthit.GetSecondHitPhiL(0), bdthit.GetSecondHitTheR(0), bdthit.GetSecondHitTheL(0), bdthit.GetLayerSecondHitPhiR(0), bdthit.GetLayerSecondHitPhiL(0), bdthit.GetLayerSecondHitTheR(0), bdthit.GetLayerSecondHitTheL(0),\
                               bdthit.Getsdphi(1), bdthit.Getsdthe(1), bdthit.GetIsTrue(1), bdthit.GetSecondHitPhiR(1), bdthit.GetSecondHitPhiL(1), bdthit.GetSecondHitTheR(1), bdthit.GetSecondHitTheL(1), bdthit.GetLayerSecondHitPhiR(1), bdthit.GetLayerSecondHitPhiL(1), bdthit.GetLayerSecondHitTheR(1), bdthit.GetLayerSecondHitTheL(1),\
                               bdthit.Getsdphi(2), bdthit.Getsdthe(2), bdthit.GetIsTrue(2), bdthit.GetSecondHitPhiR(2), bdthit.GetSecondHitPhiL(2), bdthit.GetSecondHitTheR(2), bdthit.GetSecondHitTheL(2), bdthit.GetLayerSecondHitPhiR(2), bdthit.GetLayerSecondHitPhiL(2), bdthit.GetLayerSecondHitTheR(2), bdthit.GetLayerSecondHitTheL(2),\
                               bdthit.Getsdphi(3), bdthit.Getsdthe(3), bdthit.GetIsTrue(3), bdthit.GetSecondHitPhiR(3), bdthit.GetSecondHitPhiL(3), bdthit.GetSecondHitTheR(3), bdthit.GetSecondHitTheL(3), bdthit.GetLayerSecondHitPhiR(3), bdthit.GetLayerSecondHitPhiL(3), bdthit.GetLayerSecondHitTheR(3), bdthit.GetLayerSecondHitTheL(3),\
                                ])


data = pd.DataFrame(data_array, columns=('NBDThit', 'Pt', 'Phi0', 'The0', 'PhiDC', 'ZDC', 'Alpha', 'Ecore', 'Centrality', 'Charge', 'Arm',\
                                         'sdphi0', 'sdthe0', 'IsTrue0', 'SecondHitPhiR0', 'SecondHitPhiL0', 'SecondHitTheR0', 'SecondHitTheL0', 'LayerSecondHitPhiR0', 'LayerSecondHitPhiL0', 'LayerSecondHitTheR0', 'LayerSecondHitTheL0',\
                                         'sdphi1','sdthe1','IsTrue1','SecondHitPhiR1','SecondHitPhiL1','SecondHitTheR1','SecondHitTheL1','LayerSecondHitPhiR1','LayerSecondHitPhiL1','LayerSecondHitTheR1','LayerSecondHitTheL1',\
                                         'sdphi2','sdthe2','IsTrue2','SecondHitPhiR2','SecondHitPhiL2','SecondHitTheR2','SecondHitTheL2','LayerSecondHitPhiR2','LayerSecondHitPhiL2','LayerSecondHitTheR2','LayerSecondHitTheL2',\
                                         'sdphi3','sdthe3','IsTrue3','SecondHitPhiR3','SecondHitPhiL3','SecondHitTheR3','SecondHitTheL3','LayerSecondHitPhiR3','LayerSecondHitPhiL3','LayerSecondHitTheR3','LayerSecondHitTheL3'))

8156638
2 100 -1
2 100 1
3 100 -1
2 100 1
2 100 -1
2 100 1


In [10]:
data.head()

NBDThit        Pt      Phi0      The0     PhiDC        ZDC     Alpha  \
0        1  0.314382  3.005874  1.830078  2.300781 -52.176411  0.345215   
1        1  1.835631  3.013430  1.831055  3.132812 -58.488911 -0.061127   
2       10  0.188236 -0.733406  1.872070  0.502441 -45.831791 -0.563965   
3       10  0.188236 -0.733406  1.872070  0.502441 -45.831791 -0.563965   
4       10  0.188236 -0.733406  1.872070  0.502441 -45.831791 -0.563965   

         Ecore  Centrality  Charge  ...     sdthe3  IsTrue3  SecondHitPhiR3  \
0 -9999.000000          67      -1  ... -10.000000      0.0           -99.0   
1     1.901454          67       1  ... -10.000000      0.0           -99.0   
2     0.109991          48       1  ... -10.000000      0.0           -99.0   
3     0.109991          48       1  ... -10.000000      0.0           -99.0   
4     0.109991          48       1  ...   1.256569      1.0             0.0   

   SecondHitPhiL3  SecondHitTheR3  SecondHitTheL3  LayerSecondHitPhiR3  \
0           -99.0           -99.0           -99.0                  -99   
1           -99.0           -99.0           -99.0                  -99   
2           -99.0           -99.0           -99.0                  -99   
3           -99.0           -99.0           -99.0                  -99   
4           -99.0             0.0           -99.0                  -99   

   LayerSecondHitPhiL3  LayerSecondHitTheR3  LayerSecondHitTheL3  
0                  -99                  -99                  200  
1                  -99                  -99           -224283952  
2                  -99                  -99                    0  
3                  -99                  -99                    0  
4                  -99                  -99                    0  

[5 rows x 55 columns]

In [11]:
print(data.size, data.shape, good_event_counter)

1458215 (26513, 55) 6001


In [12]:
filepath = '/sphenix/user/mitrankov/'+filename
compression_options = dict(method='zip', archive_name=f'{filename}.csv')

In [13]:
data.to_csv(f'{filepath}.zip', compression=compression_options, index=False)

OSError: Cannot save file into a non-existent directory: '/sphenix/user/mitrankov'

In [ ]:
from sklearn.ensemble import GradientBoostingClassifier
import numpy as np
from sklearn.model_selection import GridSearchCV
parameters = {
    "loss":["log_loss"],
    "learning_rate": [0.01, 0.2],
    "min_samples_split": [0.01, 0.2],
    "max_depth":[3,8],
    "max_features":["log2","sqrt"],
    "criterion": ['squared_error'],
    "n_estimators":[2]
    }
clf3 = GridSearchCV(GradientBoostingClassifier(), parameters, cv=2, n_jobs=4)

X_train = np.array([[0, 0], [1, 1], [0, 1], [1, 0], [0, 1], [1, 0]])
y_train = np.array([0, 1, 0, 0, 0, 1])

# Fit the model
clf3.fit(X_train, y_train)

# Get decision function from clf3
clf_decision = clf3.decision_function(X_train)

# Initialize log odds predictions
log_odds_predictions = np.zeros(X_train.shape[0])

# Get the best estimator
best_estimator = clf3.best_estimator_

# Iterate over trees in the best estimator
for tree in best_estimator.estimators_:
    # Get leaf indices for training data
    leaf_indices = tree[0].apply(X_train)
    # Get values at each leaf (log odds)
    leaf_values = tree[0].tree_.value[:, 0, 0]  # Accessing the log odds correctly
    # Accumulate log odds for each instance
    log_odds_predictions += leaf_values[leaf_indices] * best_estimator.learning_rate

# Final log odds with the learning rate applied
mydecision = log_odds_predictions

# Output the differences
print("My Decision (Log Odds):", mydecision)
print("Decision Function Output:", clf_decision)

# Calculate the differences
difference = np.abs(mydecision - clf_decision)
print("Differences:", difference)
